
<h1><b><i>Final Evaluation Notebook</b></i></h1>
<h3>This notebook evalutes on provided test data and generates the output csv using capped to 300 data points combining original and synthetic data which is executed in 1 epoch.</h3>

Requirements:
1. cluster.json in gdrive: https://drive.google.com/file/d/1FXM9SxGJ7o_DM_l7__5T7GxFywngxhi0/view?usp=share_link
2. preprocesssed data in gdrive: https://drive.google.com/file/d/1TX35oLZEx_VgSa6I-Oe1-EhnuDQ5JB3G/view?usp=share_link
3. For preprocessing the data for yes/no finetuning and finetuning on themes:
https://colab.research.google.com/drive/1v7ZFLfV0n5lGO8ktUOuFEbJQ9L7_zVIK

4. train_context : final preprocessed paragraph
https://drive.google.com/file/d/1yZc5AA03vnAltqPvgFmRSQIhwHz4gjqm/view?usp=share_link

In [ ]:
import collections
import json
import pandas as pd
import re
import string
import timeit
from ast import literal_eval

## To be Placed

In [ ]:
"""
For the purpose of Book Keeping

Changes Required:

org_df = pd.read_csv('/content/drive/MyDrive/train_data_passages_all.csv')

theme_list = [0,1,2]

model_checkpoint = f"nandysoham/{theme}"

------------------------------------------------------------------------
Hyperparameters:
------------------------------------------------------------------------
k_topmost = find_k_topmost(5, weighted_arr)






"""

'\nFor the purpose of Book Keeping\n\nChanges Required:\n\norg_df = pd.read_csv(\'/content/drive/MyDrive/train_data_passages_all.csv\')   \n\ntheme_list = [0,1,2]\n\nmodel_checkpoint = f"nandysoham/{theme}"\n\n------------------------------------------------------------------------\nHyperparameters:\n------------------------------------------------------------------------\nk_topmost = find_k_topmost(5, weighted_arr)  \n\n\n\n\n\n\n'

In [ ]:
# -------------------------- CONNCETING TO HUGGING FACE HUB FOR STORING OF THE MODEL ------------------------------

! pip install transformers datasets huggingface_hub

# logging in
from huggingface_hub import notebook_login
notebook_login()

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 31.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 462.8/462.8 KB 20.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 9.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 46.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.0/132.0 KB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.0/213.0 KB 9.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 KB 14.7 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


In [ ]:
# -------------------------- CONNECTING TO DRIVE + INSTALLATIONS ------------------------------

"""
Requirements:
Drive Needs to have a file names clustered.json --> Download from https://drive.google.com/file/d/1LfhA7eGlrePhdhSSelVJxGmR5rG_hx1C/view?usp=share_link

"""
# All installations here
from google.colab import drive
drive.mount('/content/drive')

!pip install scipy
from scipy.spatial import distance




# git installation
!apt install git-lfs
!git config --global user.email "nandysoham16@gmail.com"
!git config --global user.name "nandysoham"


# all imports
import tensorflow as tf
import transformers
from datasets import load_dataset, load_metric
import pandas as pd
import numpy as np
import random
from transformers import AutoTokenizer
import transformers
from transformers import TFAutoModelForQuestionAnswering
from transformers import create_optimizer
from transformers.keras_callbacks import PushToHubCallback
from tensorflow.keras.callbacks import TensorBoard
import collections
from transformers import create_optimizer

# choose a random theme
!pip3 install unidecode
from unidecode import unidecode
from datasets import load_dataset, load_metric, Dataset

import json
with open('/content/drive/MyDrive/cluster.json') as json_file:
    clusters_dict = json.load(json_file)


# clusters_dict = json.load("https://raw.githubusercontent.com/nandysoham/dev_rev_data/master/cluster.json?token=GHSAT0AAAAAAB5L2JDGV43EJHQNZGVKA6KKY66IZWQ")

clustered = clusters_dict["clusters"]
centroids = clusters_dict["centroids"]

!pip install sentence_transformers
from sentence_transformers import SentenceTransformer


# Top-k requirements
from sentence_transformers import SentenceTransformer, util
clustering_model = SentenceTransformer('all-MiniLM-L6-v2')

Mounted at /content/drive
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Reading package lists... Done
Building dependency tree       
Reading state information... Done
git-lfs is already the newest version (2.9.2-1).
The following package was automatically installed and is no longer required:
  libnvidia-common-510
Use 'apt autoremove' to remove it.
0 upgraded, 0 newly installed, 0 to remove and 27 not upgraded.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.9/235.9 KB 6.1 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 KB 4.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 24.7 MB/s eta 0:00:00
  Created wheel for sentence_transformers: filename=

In [ ]:
# Allowed to make changes.

# Pre-processing cell. You can use this cell to pre-process input data or load
# your models.

# Dummy code.

"""
Assumptions: paragraphs given
------------------------------------------
id      theme       paragraph
------------------------------------------

ASSUME THE PARAGRAPH DATA CONTAINS ALL THEMES ALL TOGETHER

"""
paragraph_dict = {}


"""
global_model: All models for the 30 themes are preloaded

--> access model through global_model[theme]

"""
global_model = {}

# Here, you can load the existing QA pairs for themes and pre-process it.
# Sample QA pairs: https://drive.google.com/file/d/1HORTMN3UrPyfcibMZIA6tVnkgQXlZfWn/view?usp=share_link
questions = []

In [ ]:
"""
============= The top-k elements pickup model Block=============

"""
passage_encoder = SentenceTransformer('facebook-dpr-ctx_encoder-single-nq-base')
query_encoder = SentenceTransformer('facebook-dpr-question_encoder-single-nq-base')



def find_k_topmost(k, weighted_arr):
  """
  INPUT : An array of weights,
  OUTPUT : Return the INDICES of the top k elements sorted in order
  """
  list_by_wt = []
  idx = 0
  for val in weighted_arr:
    list_by_wt.append([val, idx])
    idx += 1

  list_by_wt.sort(reverse=True)
  index_list = []
  for i in range(k):
    index_list.append(list_by_wt[i][1])
  # print(index_list)
  return index_list



def return_k_topmost(questions, passages):
  """
  INPUT : Dict of Questions of format     id    theme     question  and a DF of passages
  OUTPUT : List of List - for each question the list of indices of top k elements

  HYPERPARAMETER : k
  """
  passage_embeddings = passage_encoder.encode(passages)

  i=0
  all_indices = []
  for question in questions:
    query=question['question']
    query_embedding = query_encoder.encode(query)
    scores = util.dot_score(query_embedding, passage_embeddings)
    for ten in scores:
      weighted_arr = ten.numpy()
      # print(weighted_arr)
      # print(type(weighted_arr))
      k_topmost = find_k_topmost(5, weighted_arr)             # CHANGE HYPERPARAMETER OF K HERE
      all_indices.append(k_topmost)
    # print(i)
    # print(" Scores:", scores)
    # print(scores.size())
    i=i+1
  return all_indices


In [ ]:
"""
Download all paragraphs and get theme_wise
-----------------------------------------------------
  # CHANGE!!! TITLE TO THEME IF IN CASE FINAL PARAMETERS ARE DIFFERENT
  # CHANGE!!! org_df --> to the original passages csv
"""
org_df = pd.read_csv('/content/drive/MyDrive/train_context.csv')
print(org_df)





def split_by_themes(df):
  """
  INPUT : A DF having the overall data
  OUTPUT : A dictionary of DFs ordered by themes

  CHANGE OF PARAMETERS: theme vs title as per the requirements
  """
  # extracting the themes
  themes = df.theme.unique()                                                                        # CHANGE TITLE TO THEME
  paragraph_dict = {elem : pd.DataFrame() for elem in themes}
  for key in themes:
    paragraph_dict[key] = df[:][df.theme == key]                                                    # CHANGE TITLE TO THEME
  return paragraph_dict


paragraph_dict = split_by_themes(org_df)


      Unnamed: 0    id                                            context  \
0              0     1  The iPod is a line of portable media players a...   
1              1     2  Like other digital music players, iPods can se...   
2              2     3  Apple's iTunes software (and other alternative...   
3              3     4  Before the release of iOS 5, the iPod branding...   
4              4     5  In mid-2015, a new model of the iPod Touch was...   
...          ...   ...                                                ...   
1174        1174  1175  Adding new Customers# Customer records offer a...   
1175        1175  1176  Apart from customer records that get automatic...   
1176        1176  1177  Authentication to DevRev APIs requires a perso...   
1177        1177  1178  Generate a Personal Access Token (PAT)# In the...   
1178        1178  1179  Revoke a Personal Access Token# Caution: Once ...   

       theme  
0       IPod  
1       IPod  
2       IPod  
3       IPod  


In [ ]:
print(paragraph_dict.keys())

dict_keys(['IPod', '2008_Sichuan_earthquake', 'Wayback_Machine', 'Canadian_Armed_Forces', 'Cardinal_(Catholicism)', 'Human_Development_Index', 'Heresy', 'Warsaw_Pact', 'Materialism', 'Pub', 'Web_browser', 'Catalan_language', 'Paper', 'Adult_contemporary_music', 'Nanjing', 'Dialect', 'Southampton', 'The_Times', 'Immunology', 'Imamah_(Shia_doctrine)', 'Grape', 'United_States_dollar', 'Everton_F.C.', 'Hard_rock', 'Great_Plains', 'Biodiversity', 'Federal_Bureau_of_Investigation', 'Mary_(mother_of_Jesus)', 'Unknown', 'DevRev'])


In [ ]:
def process_name(name):
  name = unidecode(name)
  new_name = ""
  for ch in name:
    if(ch.isdigit() or ch.isalpha()):
      new_name += ch
    else:
      new_name += '_'
  return new_name


In [ ]:
# opening of yes no models
!unzip /content/drive/MyDrive/yes_no_model_finetuned.zip



def f1_metric(y_true, y_pred):
    true_positives = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    possible_positives = K.sum(K.round(K.clip(y_true, 0, 1)))
    predicted_positives = K.sum(K.round(K.clip(y_pred, 0, 1)))
    precision = true_positives / (predicted_positives + K.epsilon())
    recall = true_positives / (possible_positives + K.epsilon())
    f1_val = 2*(precision*recall)/(precision+recall+K.epsilon())
    return f1_val

def create_yesno_model():
  yn_model = Sequential()
  yn_model.add(Dense(units=512, activation='relu', input_shape=(768,)))
  yn_model.add(Dense(units = 512, activation='relu'))
  # model.add(Dropout(0.2))
  yn_model.add(Dense(units = 256, activation='relu'))
  yn_model.add(Dense(units = 128, activation='relu',kernel_regularizer=l2(0.05), bias_regularizer=l2(0.05)))
  yn_model.add(Dense(units = 2, activation='softmax'))

  yn_model.compile(loss='binary_crossentropy', metrics=['accuracy', f1_metric], optimizer='adam')
  return yn_model



Archive:  /content/drive/MyDrive/yes_no_model_finetuned.zip
   creating: yes_no_model/
   creating: yes_no_model/Paper/
  inflating: yes_no_model/Paper/cp.ckpt.data-00000-of-00001  
  inflating: yes_no_model/Paper/cp.ckpt.index  
  inflating: yes_no_model/Paper/checkpoint  
   creating: yes_no_model/Wayback_Machine/
  inflating: yes_no_model/Wayback_Machine/cp.ckpt.data-00000-of-00001  
  inflating: yes_no_model/Wayback_Machine/cp.ckpt.index  
  inflating: yes_no_model/Wayback_Machine/checkpoint  
   creating: yes_no_model/Human_Development_Index/
  inflating: yes_no_model/Human_Development_Index/cp.ckpt.data-00000-of-00001  
  inflating: yes_no_model/Human_Development_Index/cp.ckpt.index  
  inflating: yes_no_model/Human_Development_Index/checkpoint  
   creating: yes_no_model/Adult_contemporary_music/
  inflating: yes_no_model/Adult_contemporary_music/cp.ckpt.data-00000-of-00001  
  inflating: yes_no_model/Adult_contemporary_music/cp.ckpt.index  
  inflating: yes_no_model/Adult_conte

In [ ]:

def ret_cluster(theme):
  test_embedding = clustering_model.encode(theme)
  cluster_no = 0
  cluster_val = distance.cosine(centroids[0], test_embedding)
  for i, item in enumerate(centroids):
    # print(i)
    # print(item)
    val = distance.cosine(item, test_embedding)
    if( val < cluster_val):
      cluster_no = i
      cluster_val = val

  return cluster_no

In [ ]:
"""
================== YES/NO BOOLEAN MODEL BLOCK ==================
REQUIREMENTS : LOAD THE ZIP MODEL either directly or from google drive
                model path name changed to final_yes_no_model


"""




# Save & Load: https://www.tensorflow.org/tutorials/keras/save_and_load
import keras.backend as K
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dropout
from keras.regularizers import l2

!unzip /content/drive/MyDrive/yes_no_model_base.zip
checkpoint_path = "yes_no_model_base/cp.ckpt"              # CHANGED THE NAME, No duplicates should exist in the system



new_model = Sequential()
new_model.add(Dense(units=512, activation='relu', input_shape=(768,)))
new_model.add(Dense(units = 512, activation='relu'))
# model.add(Dropout(0.2))
new_model.add(Dense(units = 256, activation='relu'))
new_model.add(Dense(units = 128, activation='relu',kernel_regularizer=l2(0.05), bias_regularizer=l2(0.05)))
new_model.add(Dense(units = 2, activation='softmax'))

new_model.compile(loss='binary_crossentropy', metrics=['accuracy', f1_metric], optimizer='adam')
new_model.load_weights(checkpoint_path)





Archive:  /content/drive/MyDrive/yes_no_model_base.zip
   creating: yes_no_model_base/
  inflating: yes_no_model_base/cp.ckpt.data-00000-of-00001  
  inflating: yes_no_model_base/cp.ckpt.index  
  inflating: yes_no_model_base/checkpoint  


In [ ]:
"""
Downloading all the models for 30 themes in one go!
CHANGE OF PARAMETERS : THEME_LIST
"""


# actual themes
theme_list = ['2008_Sichuan_earthquake',
 'Adult_contemporary_music',
 'Biodiversity',
 'Canadian_Armed_Forces',
 'Cardinal_(Catholicism)',
 'Catalan_language',
 'DevRev',
 'Dialect',
 'Everton_F.C.',
 'Federal_Bureau_of_Investigation',
 'Grape',
 'Great_Plains',
 'Hard_rock',
 'Heresy',
 'Human_Development_Index',
 'IPod',
 'Imamah_(Shia_doctrine)',
 'Immunology',
 'Mary_(mother_of_Jesus)',
 'Materialism',
 'Nanjing',
 'Paper',
 'Pub',
 'Southampton',
 'The_Times',
 'United_States_dollar',
 'Unknown',
 'Warsaw_Pact',
 'Wayback_Machine',
 'Web_browser']                                # CHANGE THE LIST WITH THE THEMES LIST GIVEN



test_list = ['2008_Sichuan_earthquake',
 'Adult_contemporary_music',
 'Canadian_Armed_Forces',
 'Cardinal_(Catholicism)',
 'Catalan_language',
 'Heresy',
 'Human_Development_Index',
 'IPod',
 'Materialism',
 'Paper',
 'Pub',
 'Warsaw_Pact',
 'Wayback_Machine',
 'Web_browser']


# for theme in theme_list:
#   sen_theme = process_name(theme)
#   model_checkpoint = f"recklessrecursion/{sen_theme}-clustered"          # CHANGE THE CHECKPOINT BY THEME
#   # model_checkpoint = f"nandysoham/{theme}-clustered"


#   # yn model
#   checkpoint_path = f"yes_no_model/{theme}/cp.ckpt"
#   ynmodel = create_yesno_model()



#   # now note that the models can be saved in huggingface in a diffeent name
#   if theme in test_list:
#     ynmodel.load_weights(checkpoint_path)
#     model = TFAutoModelForQuestionAnswering.from_pretrained(model_checkpoint)
#     tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
#     global_model[theme] = {
#         "model_checkpoint" : model_checkpoint,
#         "model" : model,
#         "tokenizer" : tokenizer,
#         "ynmodel" : ynmodel
#     }

#   else:
#     cluster_no = ret_cluster(theme)
#     model_checkpoint = f"nandysoham16/{cluster_no}-clustered_aug"
#     model = TFAutoModelForQuestionAnswering.from_pretrained(model_checkpoint)
#     tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
#     global_model[theme] = {
#         "model_checkpoint" : model_checkpoint,
#         "model" : model,
#         "tokenizer" : tokenizer,
#         "ynmodel" : new_model
#     }


# print(global_model)

In [ ]:
def get_theme_model(theme):
  """
  Utility to extract the theme from the dictionary
  """
  sen_theme = process_name(theme)
  model_checkpoint = f"deepiit98/{sen_theme}-clustered"          # CHANGE THE CHECKPOINT BY THEME
  # model_checkpoint = f"nandysoham/{theme}-clustered"


  # yn model
  checkpoint_path = f"yes_no_model/{theme}/cp.ckpt"
  ynmodel = create_yesno_model()



  # now note that the models can be saved in huggingface in a diffeent name
  if theme in test_list:
    ynmodel.load_weights(checkpoint_path)
    print("done with manual")
    model = TFAutoModelForQuestionAnswering.from_pretrained(model_checkpoint)
    tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
    finetuned_model = {
        "model_checkpoint" : model_checkpoint,
        "model" : model,
        "tokenizer" : tokenizer,
        "ynmodel" : ynmodel
    }

  else:
    cluster_no = ret_cluster(theme)
    model_checkpoint = f"nandysoham16/{cluster_no}-clustered_aug"
    model = TFAutoModelForQuestionAnswering.from_pretrained(model_checkpoint)
    tokenizer = AutoTokenizer.from_pretrained(model_checkpoint)
    finetuned_model = {
        "model_checkpoint" : model_checkpoint,
        "model" : model,
        "tokenizer" : tokenizer,
        "ynmodel" : new_model
    }
  return finetuned_model

In [ ]:

"""
==================== PREPROCESSING FOR YES/NO MODEL BLOCK ====================
"""

from sentence_transformers import SentenceTransformer
fair_model = SentenceTransformer('paraphrase-MiniLM-L6-v2')
from sklearn.preprocessing import normalize

def ret_embeddings(df):
  """
  INPUT:
    df --> a dataframe
    -----------------------------------
    text      map       theme
    -----------------------------------

  OUTPUT:
    ndarray containing embeddings of question and answer fused together


  """
  question_feed = np.array((df["question"]))
  context_feed = np.array((df["text"]))
  ques_embeddings=fair_model.encode(question_feed)
  context_embeddings = fair_model.encode(context_feed)
  input = []
  r_len = len(ques_embeddings)
  c_len = len(ques_embeddings[0])
  for i in range(r_len):
    element = []
    for j in range(c_len):
      element.append(ques_embeddings[i][j])

    for j in range(c_len):
      element.append(context_embeddings[i][j])

    input.append(element)
  x_input = np.array(input)
  x_input=normalize(input)
  return x_input






def return_aggregrate(questions, paragraph, k_list):
  """
  INPUT : List of questions, DF paragraph, k_list containging lists of size k for each question
  OUTPUT: List of dictionary for each question having
    {"text" : full_text_of_k_paras, "map" : the starting indices of each para, "theme" }
  """
  sub_input = []
  idx = 0;
  for ques in questions:
    entry = {}
    entry["question"] = ques["question"]
    start_pos = []
    full_para = ""
    for id in k_list[idx]:
      start_pos.append(len(full_para))
      full_para += (paragraph[id])

    entry["text"] = full_para
    entry["map"] = start_pos
    entry["theme"] = ques["theme"]
    sub_input.append(entry)
    idx+=1
  return sub_input


In [ ]:
"""
==================== SUBPART 2 MODEL  =====================
Based on a standard distilbert model

"""


from transformers import AutoTokenizer, TFAutoModelForQuestionAnswering
org_model_id = "distilbert-base-uncased-finetuned-squad"
path = f"Rocketknight1/{org_model_id}"
tokenizer = AutoTokenizer.from_pretrained(path)
model = TFAutoModelForQuestionAnswering.from_pretrained(path)

max_length = 384  # The maximum length of a feature (question and context)
doc_stride = 128  # The allowed overlap between two part of the context when splitting is performed.
batch_size = 16


pad_on_right = tokenizer.padding_side=="right"

def prepare_validation_features(examples):
    # Tokenize our examples with truncation and maybe padding, but keep the overflows using a stride. This results
    # in one example possible giving several features when a context is long, each of those features having a
    # context that overlaps a bit the context of the previous feature.
    tokenized_examples = tokenizer(
        examples["question" if pad_on_right else "context"],
        examples["context" if pad_on_right else "question"],
        truncation="only_second" if pad_on_right else "only_first",
        max_length=max_length,
        stride=doc_stride,
        return_overflowing_tokens=True,
        return_offsets_mapping=True,
        padding="max_length",
    )

    # Since one example might give us several features if it has a long context, we need a map from a feature to
    # its corresponding example. This key gives us just that.
    sample_mapping = tokenized_examples.pop("overflow_to_sample_mapping")

    # We keep the example_id that gave us this feature and we will store the offset mappings.
    tokenized_examples["example_id"] = []

    for i in range(len(tokenized_examples["input_ids"])):
        # Grab the sequence corresponding to that example (to know what is the context and what is the question).
        sequence_ids = tokenized_examples.sequence_ids(i)
        context_index = 1 if pad_on_right else 0

        # One example can give several spans, this is the index of the example containing this span of text.
        sample_index = sample_mapping[i]
        tokenized_examples["example_id"].append(examples["id"][sample_index])

        # Set to None the offset_mapping that are not part of the context so it's easy to determine if a token
        # position is part of the context or not.
        tokenized_examples["offset_mapping"][i] = [
            (o if sequence_ids[k] == context_index else None)
            for k, o in enumerate(tokenized_examples["offset_mapping"][i])
        ]

    return tokenized_examples


squad_v2 = False

from tqdm.auto import tqdm
import collections
import numpy as np


def postprocess_qa_predictions(
    examples,
    features,
    all_start_logits,
    all_end_logits,
    n_best_size=20,
    max_answer_length=30,
):
    # Build a map example to its corresponding features.
    example_id_to_index = {k: i for i, k in enumerate(examples["id"])}
    features_per_example = collections.defaultdict(list)
    for i, feature in enumerate(features):
        features_per_example[example_id_to_index[feature["example_id"]]].append(i)

    # The dictionaries we have to fill.
    predictions = collections.OrderedDict()

    # Logging.
    print(
        f"Post-processing {len(examples)} example predictions split into {len(features)} features."
    )

    # Let's loop over all the examples!
    for example_index, example in enumerate(tqdm(examples)):
        # Those are the indices of the features associated to the current example.
        feature_indices = features_per_example[example_index]

        min_null_score = None  # Only used if squad_v2 is True.
        valid_answers = []

        context = example["context"]
        # Looping through all the features associated to the current example.
        for feature_index in feature_indices:
            # We grab the predictions of the model for this feature.
            start_logits = all_start_logits[feature_index]
            end_logits = all_end_logits[feature_index]
            # This is what will allow us to map some the positions in our logits to span of texts in the original
            # context.
            offset_mapping = features[feature_index]["offset_mapping"]

            # Update minimum null prediction.
            cls_index = features[feature_index]["input_ids"].index(
                tokenizer.cls_token_id
            )
            feature_null_score = start_logits[cls_index] + end_logits[cls_index]
            if min_null_score is None or min_null_score < feature_null_score:
                min_null_score = feature_null_score

            # Go through all possibilities for the `n_best_size` greater start and end logits.
            start_indexes = np.argsort(start_logits)[
                -1 : -n_best_size - 1 : -1
            ].tolist()
            end_indexes = np.argsort(end_logits)[-1 : -n_best_size - 1 : -1].tolist()
            for start_index in start_indexes:
                for end_index in end_indexes:
                    # Don't consider out-of-scope answers, either because the indices are out of bounds or correspond
                    # to part of the input_ids that are not in the context.
                    if (
                        start_index >= len(offset_mapping)
                        or end_index >= len(offset_mapping)
                        or not offset_mapping[start_index]
                        or not offset_mapping[end_index]
                    ):
                        continue
                    # Don't consider answers with a length that is either < 0 or > max_answer_length.
                    if (
                        end_index < start_index
                        or end_index - start_index + 1 > max_answer_length
                    ):
                        continue
                    start_char = offset_mapping[start_index][0]
                    end_char = offset_mapping[end_index][1]
                    valid_answers.append(
                        {
                            "score": start_logits[start_index] + end_logits[end_index],
                            "text": context[start_char:end_char],
                            "Starts" : start_char,
                            "Ends" : end_char
                        }
                    )

        if len(valid_answers) > 0:
            best_answer = sorted(valid_answers, key=lambda x: x["score"], reverse=True)[
                0
            ]
        else:
            # In the very rare edge case we have not a single non-null prediction, we create a fake prediction to avoid
            # failure.
            best_answer = {"text": "", "score": 0.0, "Starts":-1, "Ends": -1}

        # Let's pick our final answer: the best one or the null answer (only for squad_v2)
        if not squad_v2:
            predictions[example["id"]] = {"text_answer" : best_answer["text"], "starts" : best_answer["Starts"], "ends" : best_answer["Ends"]}
        else:
            answer = {
                "text_answer" : best_answer["text"] if best_answer["score"] > min_null_score else "",
                "starts" :  best_answer["Starts"] if best_answer["score"] > min_null_score else -1 ,
                "ends" : best_answer["Ends"] if best_answer["score"] > min_null_score else -1,
            }
            predictions[example["id"]] = answer

    return predictions

final_df = {}
def run_model(datasets, theme,model_finetuned):
  global model
  global tokenizer
  global org_model_id
  # model_finetuned = get_theme_model(theme)
  org_model_id = model_finetuned["model_checkpoint"]
  model = model_finetuned["model"]
  tokenizer = model_finetuned["tokenizer"]

  validation_features = datasets.map(
      prepare_validation_features,
      batched=True,
      remove_columns=datasets.column_names,
  )


  validation_dataset = model.prepare_tf_dataset(
      validation_features,
      shuffle=False,
      batch_size=batch_size,
  )

  raw_predictions = model.predict(validation_dataset)

  final_predictions = postprocess_qa_predictions(
    datasets,
    validation_features,
    raw_predictions["start_logits"],
    raw_predictions["end_logits"],
  )

  return final_predictions






All model checkpoint layers were used when initializing TFDistilBertForQuestionAnswering.

All the layers of TFDistilBertForQuestionAnswering were initialized from the model checkpoint at Rocketknight1/distilbert-base-uncased-finetuned-squad.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFDistilBertForQuestionAnswering for predictions without further training.


In [ ]:
"""
Making k_list and final_predictions global parameters, as retraining them would cause havoc
"""
k_list =[]
final_predictions = {}
!mkdir stored_results

In [ ]:
"""
Assumptions:

questions:
type: List of dicts
---------------------------------------------
id    theme     question
---------------------------------------------


Requirements:

pred_out :
type: List of dicts
---------------------------------------------
question_id     paragraph_id    answers
---------------------------------------------

"""

from collections import OrderedDict

def pred_theme_ans(questions_org, theme_model, total_pred_out):
  # creating the map of questions here
  pred_out=[]
  q_dict = {}
  idx = 0
  questions = []
  q_map = {}
  uniqueidx = 0
  for q in questions_org:
    if q["question"] in q_dict:
      q_map[q_dict[q["question"]]].append(idx)
      idx += 1
    else:
      questions.append(q)
      q_dict[q["question"]] = uniqueidx
      q_map[uniqueidx] = [idx]
      uniqueidx+=1
      idx += 1


  # print(q_map)
  print("len of org questions", len(questions_org))
  print("len of questions", len(questions))
  theme = questions[0]["theme"]
  paragraph_df = paragraph_dict[theme]



  # paragraph list from the custom list
  para_org = list(paragraph_df["context"])

  p_dict = {}
  idx = 0
  paragraph = []
  p_map = {}
  unique = 0
  for p in para_org:
    if p in p_dict:
      idx += 1
      continue
    else:

      paragraph.append(p)
      p_dict[p] = idx
      p_map[unique] = idx
      unique += 1
      idx += 1


  print("len of org set of paras", len(para_org))
  print("len of para" , len(paragraph))

  # print(paragraph)


  # print(p_map)
  passages=[]
  for i in range(len(paragraph)):
    passages.append(theme+" [SEP] "+paragraph[i])
  print(questions)
  print(passages)
  global k_list

  # very time_consuming - should store it somewhere

  # uncomment in normal scenarios
  k_list = return_k_topmost(questions, passages)                     # COMMENT OUT IF YOU HAVE THIS LINE STRUCK BY AN ERROR

  # Now you have the k_list

  sub_input = return_aggregrate(questions, paragraph, k_list)

  item_maps = [i["map"] for i in  sub_input]          # to store the start position so fthe paragraphs
  x_test = ret_embeddings(pd.DataFrame(sub_input))



  # change the model here
  # pick the model up from zip file
  # pick from the global model
  # -----------------------------------------------------------------------------------
  ynmodel = theme_model["ynmodel"]
  predictions = ynmodel.predict(x_test)

  # predictions = new_model.predict(x_test)
  # print(predictions)
  idx = 0;
  for i in sub_input:
    i["isansposs"] = 1 if predictions[idx][1] > predictions[idx][0] else 0
    i["actual_idx"] = idx
    idx += 1
  global qa_df
  qa_df = pd.DataFrame(sub_input)

  # print(qa_df)
  ans_poss = [0 for i in range(len(qa_df))]
  idx = 0;
  for i in qa_df.index:
    if(qa_df["isansposs"][i] == 0):
      ans_poss[idx] = -1
    idx+=1

  feed_df = qa_df[["theme", "text", "question" , "actual_idx"]][qa_df.isansposs == 1]
  # print(feed_df)
  feed_df.rename(columns = {'text':'context'}, inplace = True)
  feed_df["id"] = [i for i in range(len(feed_df))]
  org_datasets = Dataset.from_pandas(feed_df)
  global final_predictions
  final_predictions = run_model(org_datasets,theme,theme_model)   # PASS THE THEME HERE


  idx = 0
  yes_idx = 0

  for i in range(len(questions_org)):
    pred_out.append({})
  # print(pred_out)




  for question in questions:
    # print(question["question"])
    ans = {}
    ans["question_id"] = question["id"]     # CHANGE TO ID, INDEX IS JUST FOR TESTING
    if (ans_poss[idx] == -1):
      ans["paragraph_id"] = -1
      ans["answers"] = ""
    else:

      if(len(final_predictions[yes_idx]["text_answer"])== 0):
        ans["paragraph_id"] = -1
        ans["answers"] = ""
      else:
        org_index = final_predictions[yes_idx]["starts"]

        start_set = list(item_maps[idx])
        index_list = k_list[idx]
        start_set.append(1e9)
        actal_idx = -1
        for i in range(len(start_set)):
          if(org_index < start_set[i]):
              actual_idx = index_list[i-1]
              break

        ans["paragraph_id"] = paragraph_df.iloc[p_map[actual_idx]][0] + 1          # mapping the actual answer
        # p_map[actual_idx]
        ans["answers"] = final_predictions[yes_idx]["text_answer"]
      # print(ans)
      yes_idx += 1
    # print(q_map[idx])
    for indices in q_map[idx]:
      pred_out[indices] = ans
    idx += 1

  print(len(paragraph_df))
  # print(len(pred_out))
  # for i in range(len(pred_out)):
  #   if (pred_out[i]["paragraph_id"] != -1):
  #     val = paragraph_df.iloc[pred_out[i]["paragraph_id"]][0]
  #     print("actual" , pred_out[i]["paragraph_id"])
  #     print("printed" , val)


    # you can store theme by uncommenting this line
  total_pred_out.extend(pred_out)
  pd.DataFrame(pred_out).to_csv(f"stored_results/{theme}")

###their part

In [ ]:
# NOT allowed to make changes.

# All theme prediction.
questions = json.loads(pd.read_csv("sample_input_question.csv").to_json(orient="records"))
theme_intervals = json.loads(pd.read_csv("sample_theme_interval.csv").to_json(orient="records"))
pred_out = []
theme_inf_time = {}
for theme_interval in theme_intervals:
  theme_ques = questions[int(theme_interval["start"]) - 1: int(theme_interval["end"])]
  theme = theme_ques[0]["theme"]
  # Load model fine-tuned for this theme.
  theme_model = get_theme_model(theme)
  execution_time = timeit.timeit(lambda: pred_theme_ans(theme_ques, theme_model, pred_out), number=1)
  theme_inf_time[theme_interval["theme"]] = execution_time * 1000 # in milliseconds.
pred_df = pd.DataFrame.from_records(pred_out)
pred_df.fillna(value='', inplace=True)
# Write prediction to a CSV file. Teams are required to submit this csv file.
pred_df.to_csv('sample_output_prediction.csv', index=False)

done with manual


Some layers from the model checkpoint at deepiit98/IPod-clustered were not used when initializing TFDistilBertForQuestionAnswering: ['dropout_19']
- This IS expected if you are initializing TFDistilBertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some layers of TFDistilBertForQuestionAnswering were not initialized from the model checkpoint at deepiit98/IPod-clustered and are newly initialized: ['dropout_39']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


len of org questions 221
len of questions 221
len of org set of paras 58
len of para 58
[{'id': 1, 'question': 'Which company produces the iPod?', 'theme': 'IPod'}, {'id': 2, 'question': 'When was the original iPod released?', 'theme': 'IPod'}, {'id': 3, 'question': 'How many different types of iPod are currently available?', 'theme': 'IPod'}, {'id': 4, 'question': 'What kind of device is the iPod?', 'theme': 'IPod'}, {'id': 5, 'question': 'The iPod Touch uses what kind of interface?', 'theme': 'IPod'}, {'id': 6, 'question': 'What company manufactures the iPod?', 'theme': 'IPod'}, {'id': 7, 'question': 'In addition to playing music, what other function can the iPod perform?', 'theme': 'IPod'}, {'id': 8, 'question': 'What is the smallest data capacity for an iPod product?', 'theme': 'IPod'}, {'id': 9, 'question': 'What is the largest data capacity for an iPod product?', 'theme': 'IPod'}, {'id': 10, 'question': 'Which iPod product features the smallest data storage capacity?', 'theme': '

  0%|          | 0/1 [00:00<?, ?ba/s]

31/31 [==============================] - 418s 13s/step
Post-processing 220 example predictions split into 487 features.


...

len of org questions 10
len of questions 10
len of org set of paras 21
len of para 21
[{'id': 5238, 'question': 'What is DevRev PLuG platform and what does it stand for?', 'theme': 'DevRev'}, {'id': 5239, 'question': 'What is Conversation?', 'theme': 'DevRev'}, {'id': 5240, 'question': 'What is a Ticket?', 'theme': 'DevRev'}, {'id': 5241, 'question': 'What is issue?', 'theme': 'DevRev'}, {'id': 5242, 'question': 'What is similar work modal?', 'theme': 'DevRev'}, {'id': 5243, 'question': 'What is part?', 'theme': 'DevRev'}, {'id': 5244, 'question': 'What is Rev part?', 'theme': 'DevRev'}, {'id': 5245, 'question': 'What is Dev Part?', 'theme': 'DevRev'}, {'id': 5246, 'question': 'What is a Feature?', 'theme': 'DevRev'}, {'id': 5247, 'question': 'What is Runnable?', 'theme': 'DevRev'}]
['DevRev [SEP] Welcome to DevRev PLuG platform! Our goal is to provide an easy to use experience that empowers your end users and customer facing teams with ready access to relevant information to enable mo

  0%|          | 0/1 [00:00<?, ?ba/s]

2/2 [==============================] - 20s 4s/step
Post-processing 9 example predictions split into 22 features.


  0%|          | 0/9 [00:00<?, ?it/s]

21


In [ ]:
# NOT allowed to make changes.

def normalize_answer(s):
  """Lower text and remove punctuation, articles and extra whitespace."""
  def remove_articles(text):
    regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
    return re.sub(regex, ' ', text)
  def white_space_fix(text):
    return ' '.join(text.split())
  def remove_punc(text):
    exclude = set(string.punctuation)
    return ''.join(ch for ch in text if ch not in exclude)
  def lower(text):
    return text.lower()
  return white_space_fix(remove_articles(remove_punc(lower(s))))

def get_tokens(s):
  if not s: return []
  return normalize_answer(s).split()

def calc_f1(a_gold, a_pred):
  gold_toks = get_tokens(a_gold)
  pred_toks = get_tokens(a_pred)
  common = collections.Counter(gold_toks) & collections.Counter(pred_toks)
  num_same = sum(common.values())
  if len(gold_toks) == 0 or len(pred_toks) == 0:
    # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
    return int(gold_toks == pred_toks)
  if num_same == 0:
    return 0
  precision = 1.0 * num_same / len(pred_toks)
  recall = 1.0 * num_same / len(gold_toks)
  f1 = (2 * precision * recall) / (precision + recall)
  return f1

def calc_max_f1(predicted, ground_truths):
  max_f1 = 0
  if len(ground_truths) == 0:
    return len(predicted) == 0
  for ground_truth in ground_truths:
    f1 = calc_f1(predicted, ground_truth)
    max_f1 = max(max_f1, f1)
  return max_f1

In [ ]:
# NOT allowed to make changes.

# Evaluation methodology.
metrics = {}
pred = pd.read_csv("sample_output_prediction.csv")
pred.fillna(value='', inplace=True)
truth = pd.read_csv("sample_ground_truth.csv")
truth.fillna(value='', inplace=True)
truth.paragraph_id = truth.paragraph_id.apply(literal_eval)
truth.answers = truth.answers.apply(literal_eval)
questions = pd.read_csv("sample_input_question.csv")
for idx in pred.index:
  q_id = pred["question_id"][idx]
  q_rows = questions.loc[questions['id'] == q_id].iloc[-1]
  theme = q_rows["theme"]
  predicted_paragraph = pred["paragraph_id"][idx]
  predicted_ans = pred["answers"][idx]

  if theme not in metrics.keys():
    metrics[theme] = {"true_positive": 0, "true_negative": 0, "total_predictions": 0, "f1_sum": 0}

  truth_row = truth.loc[truth['question_id'] == q_id].iloc[-1]
  truth_paragraph_id = [ int(i) for i in truth_row["paragraph_id"] ]
  if predicted_paragraph in truth_paragraph_id:
    # Increase TP for that theme.
    metrics[theme]["true_positive"] = metrics[theme]["true_positive"] + 1
  # -1 prediction in case there is no paragraph which can answer the query.
  if predicted_paragraph == -1 and truth_row["paragraph_id"] == []:
    # Increase TN.
    metrics[theme]["true_negative"] = metrics[theme]["true_negative"] + 1
  # Increase total predictions for that theme.
  metrics[theme]["total_predictions"] = metrics[theme]["total_predictions"] + 1
  f1 = calc_max_f1(predicted_ans, truth_row["answers"])
  metrics[theme]["f1_sum"] = metrics[theme]["f1_sum"] + f1

FileNotFoundError: ignored

In [ ]:
# NOT allowed to make changes.

# Final score.
inf_time_threshold = 1000.0 # milliseconds.
final_para_score = 0.0
final_qa_score = 0.0
# Weight would stay hidden from teams.
theme_weights = {"Kubernetes": 0.5, "ChatGPT": 0.4, "Football world cup": 0.1}
for theme in metrics:
  inf_time_score = 1.0
  metric = metrics[theme]
  para_score = (metric["true_positive"] + metric["true_negative"]) / metric["total_predictions"]
  qa_score = metric["f1_sum"] / metric["total_predictions"]
  avg_inf_time = theme_inf_time[theme] / metric["total_predictions"]
  if avg_inf_time > inf_time_threshold:
    inf_time_score = inf_time_threshold / avg_inf_time
  final_qa_score += theme_weights[theme] * inf_time_score * qa_score
  final_para_score += theme_weights[theme] * inf_time_score * para_score
print (final_para_score)
print (final_qa_score)


In [ ]:
!zip -r stored_results_cpu stored_results

  adding: stored_results/ (stored 0%)
  adding: stored_results/Wayback_Machine (deflated 55%)
  adding: stored_results/The_Times (deflated 62%)
  adding: stored_results/Imamah_(Shia_doctrine) (deflated 62%)
  adding: stored_results/Biodiversity (deflated 66%)
  adding: stored_results/Great_Plains (deflated 65%)
  adding: stored_results/Web_browser (deflated 59%)
  adding: stored_results/Materialism (deflated 60%)
  adding: stored_results/Hard_rock (deflated 64%)
  adding: stored_results/Human_Development_Index (deflated 58%)
  adding: stored_results/Federal_Bureau_of_Investigation (deflated 65%)
  adding: stored_results/Dialect (deflated 65%)
  adding: stored_results/Warsaw_Pact (deflated 58%)
  adding: stored_results/Adult_contemporary_music (deflated 60%)
  adding: stored_results/Immunology (deflated 62%)
  adding: stored_results/Catalan_language (deflated 60%)
  adding: stored_results/2008_Sichuan_earthquake (deflated 54%)
  adding: stored_results/Pub (deflated 58%)
  adding: stored